In [1]:
# 1_스트림릿 설치
!pip install -q streamlit
!pip install streamlit_chat

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.1/8.1 MB 18.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 207.3/207.3 kB 11.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.8/5.8 MB 28.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 83.0/83.0 kB 2.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.7/62.7 kB 2.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 6.6 MB/s eta 0:00:00


In [2]:
# 2_스트림릿 버전 확인
!pip list | grep streamlit

streamlit                        1.33.0
streamlit-chat                   0.1.1


In [33]:
# 3_API 출력 테스트 (개인 키 정보를 변경하여 결과 확인)
import base64
import json
import http.client
import ssl
import requests
import re

class CompletionExecutor:
    def __init__(self, host, api_key, api_key_primary_val, request_id):
        self._host = host
        self._api_key = api_key
        self._api_key_primary_val = api_key_primary_val
        self._request_id = request_id

    def execute(self, completion_request):
        headers = {
            'X-NCP-CLOVASTUDIO-API-KEY': self._api_key,
            'X-NCP-APIGW-API-KEY': self._api_key_primary_val,
            'X-NCP-CLOVASTUDIO-REQUEST-ID': self._request_id,
            'Content-Type': 'application/json; charset=utf-8',
        }
        # Initialize result variable

        response = requests.post(self._host + '/testapp/v1/chat-completions/HCX-003',headers=headers, json=completion_request, stream=False)
        json_data = json.loads(response.text)
        print(json_data['result']['message']['content'])


if __name__ == '__main__':
    completion_executor = CompletionExecutor(
        host='https://clovastudio.stream.ntruss.com',
        api_key='키정보 변경',
        api_key_primary_val='키정보 변경',
        request_id='103f6aaf-fee1-4884-a5bf-7628873adb7e'
    )


    preset_text = [{"role":"system","content":"- 키워드를 포함하여 이메일 내용을 생성합니다. \r\n- 메일 제목과 본문 내용을 출력합니다. \r\n- 아래 예제와 유사한 포맷으로 작성합니다. \r\n- 예제 \r\n키워드: \r\n* 주제: 업무 협조 \r\n* 요구사항: 요청하신 내용으로 작업했습니다. 확인해주세요. \r\n* 발신자: 임소희 \r\n* 수신인: 최주희 \r\n제목: 작업 내용 확인 \r\n메일: 안녕하세요 최주희님, 저희 회사에서 진행하고 있는 프로젝트에 대해 말씀드리려고 합니다. \r\n현재 개발중인 웹사이트가 있는데 혹시 괜찮으시다면 디자인 시안을 한번 봐주실 수 있을까요? \r\n가능하시다면 오늘 오후 3시쯤 뵙고 싶습니다. \r\n감사합니다. \r\n임소희 드림\r"},{"role":"user","content":"키워드:\r\n* 주제: 미팅 파일 공유\r\n* 요구사항: 미팅때 보여주셨던 파일을 보내주세요.\r\n* 발신자: 김사랑\r\n* 수신인: 유하나\r"}]
    request_data = {
        'messages': preset_text,
        'topP': 0.8,
        'topK': 0,
        'maxTokens': 300,
        'temperature': 0.3,
        'repeatPenalty': 5.0,
        'stopBefore': [],
        'includeAiFilters': True,
        'seed': 0
    }

    response_text=completion_executor.execute(request_data)

제목 : 미팅 때 보여주신 파일 전달 부탁드립니다.

안녕하세요 유하나 님, 

지난 주 금요일에 있었던 미팅 때 발표하셨던 자료들을 받아보지 못해서 이렇게 메일 드립니다. 다음 회의 때 참고할 예정이니 가능하시다면 빠른 회신 부탁 드리겠습니다.

혹시 어떤 파일인지 기억이 안나신다면 다시 설명 드릴테니 언제든지 연락 주세요.

그럼 좋은 하루 보내세요.

김사랑 드림


In [4]:
# 4. Streamlit을 활용한 챗봇 UI 제작 (개인 키 정보를 변경하여 결과 확인)
%%writefile app.py
import streamlit as st
from streamlit_chat import message
import base64
import json
import http.client
import ssl
import requests
import re

class CompletionExecutor:
    def __init__(self, host, api_key, api_key_primary_val, request_id):
        self._host = host
        self._api_key = api_key
        self._api_key_primary_val = api_key_primary_val
        self._request_id = request_id

    def execute(self, completion_request):
        headers = {
            'X-NCP-CLOVASTUDIO-API-KEY': self._api_key,
            'X-NCP-APIGW-API-KEY': self._api_key_primary_val,
            'X-NCP-CLOVASTUDIO-REQUEST-ID': self._request_id,
            'Content-Type': 'application/json; charset=utf-8',
        }
        response = requests.post(self._host + '/testapp/v1/chat-completions/HCX-003',headers=headers, json=completion_request, stream=False)
        try:
           json_data = json.loads(response.text)
           print("JSON parsing successful.")
        except json.JSONDecodeError as e:
           print("JSON parsing failed:", e)

        return json_data['result']['message']['content']

st.title("HyperCLOVA X를 활용한 이메일 작성✉️")

if 'generated' not in st.session_state:
    st.session_state['generated'] = []

if 'past' not in st.session_state:
    st.session_state['past'] = []

with st.form('form', clear_on_submit=True):
    user_input = st.text_area('You: ', '', key='input',height=200)
    submitted = st.form_submit_button('Send')
    if submitted and user_input:
        with st.spinner("Waiting for HyperCLOVA..."):

            completion_executor = CompletionExecutor(
                host='https://clovastudio.stream.ntruss.com',
                api_key='개인키정보',
                api_key_primary_val='개인키정보',
                request_id='103f6aaf-fee1-4884-a5bf-7628873adb7e'
            )

            preset_text = [{"role":"system","content":"- 키워드를 포함하여 이메일 내용을 생성합니다. \r\n- 메일 제목과 본문 내용을 출력합니다. \r\n- 아래 예제와 유사한 포맷으로 작성합니다. \r\n- 예제 \r\n키워드: \r\n* 주제: 업무 협조 \r\n* 요구사항: 요청하신 내용으로 작업했습니다. 확인해주세요. \r\n* 발신자: 임소희 \r\n* 수신인: 최주희 \r\n제목: 작업 내용 확인 \r\n메일: 안녕하세요 최주희님, 저희 회사에서 진행하고 있는 프로젝트에 대해 말씀드리려고 합니다. \r\n현재 개발중인 웹사이트가 있는데 혹시 괜찮으시다면 디자인 시안을 한번 봐주실 수 있을까요? \r\n가능하시다면 오늘 오후 3시쯤 뵙고 싶습니다. \r\n감사합니다. \r\n임소희 드림\r"},{"role":"user","content":user_input}]
            request_data = {
                'messages': preset_text,
                'topP': 0.8,
                'topK': 0,
                'maxTokens': 300,
                'temperature': 0.3,
                'repeatPenalty': 5.0,
                'stopBefore': [],
                'includeAiFilters': True,
                'seed': 0
            }

            response_text=completion_executor.execute(request_data)
            st.session_state.past.append(user_input)
            st.session_state.generated.append(response_text)

    if st.session_state['generated']:
        for i in range(len(st.session_state['generated'])-1, -1, -1):
            message(st.session_state['past'][i], is_user=True, key=str(i) + '_user')
            message(st.session_state["generated"][i], key=str(i))


Writing app.py


In [9]:
# 4-1. Streamlit을 활용한 챗봇 UI 제작 - 파라미터 조절 기능 추가하기 (개인 키 정보를 변경하여 결과 확인)
import streamlit as st
from streamlit_chat import message
import base64
import json
import http.client
import ssl
import requests
import re

class CompletionExecutor:
    def __init__(self, host, api_key, api_key_primary_val, request_id):
        self._host = host
        self._api_key = api_key
        self._api_key_primary_val = api_key_primary_val
        self._request_id = request_id

    def execute(self, completion_request):
        headers = {
            'X-NCP-CLOVASTUDIO-API-KEY': self._api_key,
            'X-NCP-APIGW-API-KEY': self._api_key_primary_val,
            'X-NCP-CLOVASTUDIO-REQUEST-ID': self._request_id,
            'Content-Type': 'application/json; charset=utf-8',
        }
        response = requests.post(self._host + '/testapp/v1/chat-completions/HCX-003',headers=headers, json=completion_request, stream=False)
        try:
           json_data = json.loads(response.text)
           print("JSON parsing successful.")
        except json.JSONDecodeError as e:
           print("JSON parsing failed:", e)

        return json_data['result']['message']['content']

st.title("HyperCLOVA X를 활용한 이메일 작성✉️")

with st.sidebar:
  st.sidebar.title('⚙️파라미터 설정값 조정')
  topP_value = st.slider('Select top P', 0.0, 1.0,0.8)
  topK_value = st.slider('Select top K', 0, 128,0)
  token_value = st.slider('Select maximum tokens?', 0, 4096,300)
  temperature_value = st.slider('Select Temperature', 0.0, 1.0,0.3)
  repeatPenalty_value = st.slider('Select Temperature', 0.0, 10.0,5.0)

if 'generated' not in st.session_state:
    st.session_state['generated'] = []

if 'past' not in st.session_state:
    st.session_state['past'] = []

with st.form('form', clear_on_submit=True):
    user_input = st.text_area('You: ', '', key='input',height=200)
    submitted = st.form_submit_button('Send')
    if submitted and user_input:
        with st.spinner("Waiting for HyperCLOVA..."):

            completion_executor = CompletionExecutor(
                host='https://clovastudio.stream.ntruss.com',
                api_key='개인키정보',
                api_key_primary_val='개인키정보',
                request_id='103f6aaf-fee1-4884-a5bf-7628873adb7e'
            )

            preset_text = [{"role":"system","content":"- 키워드를 포함하여 이메일 내용을 생성합니다. \r\n- 메일 제목과 본문 내용을 출력합니다. \r\n- 아래 예제와 유사한 포맷으로 작성합니다. \r\n- 예제 \r\n키워드: \r\n* 주제: 업무 협조 \r\n* 요구사항: 요청하신 내용으로 작업했습니다. 확인해주세요. \r\n* 발신자: 임소희 \r\n* 수신인: 최주희 \r\n제목: 작업 내용 확인 \r\n메일: 안녕하세요 최주희님, 저희 회사에서 진행하고 있는 프로젝트에 대해 말씀드리려고 합니다. \r\n현재 개발중인 웹사이트가 있는데 혹시 괜찮으시다면 디자인 시안을 한번 봐주실 수 있을까요? \r\n가능하시다면 오늘 오후 3시쯤 뵙고 싶습니다. \r\n감사합니다. \r\n임소희 드림\r"},{"role":"user","content":user_input}]
            request_data = {
                'messages': preset_text,
                'topP': topP_value,
                'topK': topK_value,
                'maxTokens': token_value,
                'temperature': temperature_value,
                'repeatPenalty': repeatPenalty_value,
                'stopBefore': [],
                'includeAiFilters': True,
                'seed': 0
            }

            response_text=completion_executor.execute(request_data)
            st.session_state.past.append(user_input)
            st.session_state.generated.append(response_text)

    if st.session_state['generated']:
        for i in range(len(st.session_state['generated'])-1, -1, -1):
            message(st.session_state['past'][i], is_user=True, key=str(i) + '_user')
            message(st.session_state["generated"][i], key=str(i))

Overwriting app.py


In [10]:
# 5. 터널링
import urllib
print("Password/Enpoint IP for localtunnel is:",urllib.request.urlopen('https://ipv4.icanhazip.com').read().decode('utf8').strip("\n"))

Password/Enpoint IP for localtunnel is: 34.133.210.108


In [11]:
#6. localtunnel
!npm install localtunnel

npm WARN saveError ENOENT: no such file or directory, open '/content/package.json'
npm WARN enoent ENOENT: no such file or directory, open '/content/package.json'
npm WARN content No description
npm WARN content No repository field.
npm WARN content No README data
npm WARN content No license field.

+ localtunnel@2.0.2
updated 1 package and audited 36 packages in 0.541s

3 packages are looking for funding
  run `npm fund` for details

found 2 moderate severity vulnerabilities
  run `npm audit fix` to fix them, or `npm audit` for details


In [12]:
#7. Stremlit app.py 실행
!streamlit run app.py &>/content/logs.txt &

In [13]:
!npx localtunnel --port 8501

npx: installed 22 in 2.411s
your url is: https://cyan-birds-beam.loca.lt
^C
